In [1]:
import os
import numpy as np
import pandas as pd
import tensorflow as tf
from tensorflow import keras
from collections import deque
import matplotlib.pyplot as plt


from tensorflow import keras
from tensorflow.keras import layers

from tensorflow.keras.layers import *
from tensorflow.keras.models import Sequential
from tensorflow.keras.utils import to_categorical
from tensorflow.keras.callbacks import EarlyStopping, ModelCheckpoint
from tensorflow.keras.utils import plot_model
from sklearn.preprocessing import LabelEncoder

from keras.models import Model


import cv2
import mediapipe as mp

os.environ['KMP_DUPLICATE_LIB_OK']='True'



2025-05-24 15:32:38.667288: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1748100758.690432  823123 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1748100758.697681  823123 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-05-24 15:32:38.727116: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.


In [2]:
import tensorflow as tf

# TensorFlow version
tf_version = tf.__version__

# CUDA and cuDNN versions
cuda_version = tf.sysconfig.get_build_info().get("cuda_version", "Not found")
cudnn_version = tf.sysconfig.get_build_info().get("cudnn_version", "Not found")

print(f"TensorFlow version: {tf_version}")
print(f"CUDA version: {cuda_version}")
print(f"cuDNN version: {cudnn_version}")


TensorFlow version: 2.18.0
CUDA version: 12.5.1
cuDNN version: 9


In [3]:
dataset_dir = "../../UCF50"

training_ratio = 0.6
validation_ratio = 0.25
test_ratio = 0.15
# classes =['PullUps','Punch','PushUps','HighJump','JavelinThrow']
# num_classes = len(classes)

number_of_frames=15

In [4]:
def extract_ucf50_classes(dataset_dir):
    classes = [folder for folder in os.listdir(dataset_dir) if os.path.isdir(os.path.join(dataset_dir, folder))]
    return classes

classes = extract_ucf50_classes(dataset_dir)
num_classes = len(classes)

label_encoder=LabelEncoder()
label_encoder.fit(classes)


# classes = classes[:3]
# num_classes = len(classes)

LabelEncoder()

In [6]:

def get_video_paths_and_categories(root_dir):
    training_video_paths = []
    training_targets = []
    validation_video_paths = []
    validation_targets = []
    test_video_paths = []
    test_targets = []
    

    for category in classes:
        category_path = os.path.join(root_dir, category)
        
        if os.path.isdir(category_path):
            nvideos = len(os.listdir(category_path))
            if nvideos == 0:
                print(f"No videos found for category: {category}")
                continue

            
            training_count = int(nvideos * training_ratio)
            validation_count = int(nvideos * validation_ratio)
            test_count = nvideos - (training_count + validation_count) 
            
            label = label_encoder.transform([category])[0]
            
            video_files = os.listdir(category_path)
            
            
            for i in range(training_count):
                video_file = video_files[i]
                video_path = os.path.join(category_path, video_file)
                training_video_paths.append(video_path)
                training_targets.append(label)

            for i in range(training_count, training_count + validation_count):
                video_file = video_files[i]
                video_path = os.path.join(category_path, video_file)
                validation_video_paths.append(video_path)
                validation_targets.append(label)

            for i in range(training_count + validation_count, training_count + validation_count + test_count):
                video_file = video_files[i]
                video_path = os.path.join(category_path, video_file)
                test_video_paths.append(video_path)
                test_targets.append(label)

        else:
            print(f"No class found for {category}")

    return (training_video_paths, training_targets, 
            validation_video_paths, validation_targets, 
            test_video_paths, test_targets)



In [7]:

mp_pose = mp.solutions.pose
def apply_mediapipe_pose(video_path,number_of_frames=10):
 
    cap = cv2.VideoCapture(video_path)
    
    if not cap.isOpened():
        print("Error: Could not open video.")
        return []

    total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    step=total_frames//number_of_frames
    
    pose_landmarks_list = []
    
    index=-1
    frames_count=0
    with mp_pose.Pose(static_image_mode=False, min_detection_confidence=0.5, min_tracking_confidence=0.5) as pose:
        while True:
            ret, frame = cap.read()
            if not ret:
                break

            index+=1
            
            if index % step == 0 and frames_count<number_of_frames:
                frames_count+=1

                rgb_frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
                rgb_frame.flags.writeable = False

                results = pose.process(rgb_frame)

                rgb_frame.flags.writeable = True
                if results.pose_landmarks:
                    mp.solutions.drawing_utils.draw_landmarks(
                        frame, results.pose_landmarks, mp_pose.POSE_CONNECTIONS)

                    landmarks = results.pose_landmarks.landmark
                    pose_landmarks_list.append([(lm.x, lm.y, lm.z,lm.visibility) for lm in landmarks])


                #gray_frame = cv2.cvtColor(frame, cv2.COLOR_RGB2GRAY)
                # cv2.imshow('MediaPipe Pose', gray_frame)
                # cv2.imshow('MediaPipe Pose', frame)
                # if cv2.waitKey(10) & 0xFF == ord('q'):
                #     break
           
    
    #padding
            
    if len(pose_landmarks_list) < number_of_frames and len(pose_landmarks_list) > 0:
        x=-1
        while len(pose_landmarks_list) < number_of_frames:
            pose_landmarks_list.append(pose_landmarks_list[x])
            x-=1

    cap.release()
    cv2.destroyAllWindows()

    # return pose_landmarks_list
    return np.array(pose_landmarks_list)



In [8]:
def apply_mediapipe_pose_v2(video_path, number_of_frames=15):
    mp_pose = mp.solutions.pose
    cap = cv2.VideoCapture(video_path)
    
    if not cap.isOpened():
        print("Error: Could not open video.")
        return []

    total_frames = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    step = total_frames // number_of_frames
    
    pose_landmarks_list = []
    selected_frame_indices=[]
    
    
    with mp_pose.Pose(static_image_mode=False, min_detection_confidence=0.5, min_tracking_confidence=0.5) as pose:
        # Calculate the frame range for each area and choose the first frame that has pose landmarks
        for i in range(number_of_frames):
            start_frame = i * step
            end_frame = (i + 1) * step if (i + 1) < number_of_frames else total_frames
            
            # Try to find a frame with pose landmarks within the area
            frame_with_landmarks = False
            
            for frame_index in range(start_frame, end_frame):
                cap.set(cv2.CAP_PROP_POS_FRAMES, frame_index)
                ret, frame = cap.read()
                if not ret:
                    break

                # frame =cv2.resize(frame,image_shape)

                rgb_frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
                rgb_frame.flags.writeable = False
                results = pose.process(rgb_frame)

                rgb_frame.flags.writeable = True
                if results.pose_landmarks:
                    # Pose landmarks found, add the frame's landmarks to the list
                    landmarks = results.pose_landmarks.landmark
                    pose_landmarks_list.append([(lm.x, lm.y, lm.z, lm.visibility,lm.presence) for lm in landmarks])
                    selected_frame_indices.append(frame_index)
                    frame_with_landmarks = True
                    break  # Once we find the first frame with landmarks, break the loop for this area

            # If no frame with landmarks was found, we add None or some default padding (optional)
            if not frame_with_landmarks:
                return np.array([]),np.array([])

    cap.release()
    cv2.destroyAllWindows()

    # Padding if the number of frames is less than required
    # if len(pose_landmarks_list) < number_of_frames and len(pose_landmarks_list) > 0:
    #     x = -1
    #     while len(pose_landmarks_list) < number_of_frames:
    #         pose_landmarks_list.append(pose_landmarks_list[x])
    #         x -= 1

    return np.array(pose_landmarks_list),np.array(selected_frame_indices)

In [9]:


x_train, y_train, x_val, y_val, x_test, y_test = get_video_paths_and_categories(dataset_dir)
# video_paths, targets = get_video_paths_and_categories(dataset_dir)

In [10]:
len(x_train)

3992

In [1]:
# #process data sequentially

# x_train_data = []
# y_train_data = []
# x_val_data = []
# y_val_data = []
# x_test_data = []
# y_test_data = []

# for i in range(len(x_train)):
#     video_path=x_train[i]
#     pose_landmarks = apply_mediapipe_pose(video_path,number_of_frames)
#     target = y_train[i]
#     if len(pose_landmarks) == number_of_frames:
#         x_train_data.append(pose_landmarks)
#         y_train_data.append(target)
        
# for i in range(len(x_val)):
#     video_path=x_val[i]
#     pose_landmarks = apply_mediapipe_pose(video_path,number_of_frames)
#     target = y_val[i]
#     if len(pose_landmarks) == number_of_frames:
#         x_val_data.append(pose_landmarks)
#         y_val_data.append(target)
        
# for i in range(len(x_test)):
#     video_path=x_test[i]
#     pose_landmarks = apply_mediapipe_pose(video_path,number_of_frames)
#     target = y_test[i]
#     if len(pose_landmarks) == number_of_frames:
#         x_test_data.append(pose_landmarks)
#         y_test_data.append(target)
        
# x_train_data = np.array(x_train_data)
# y_train_data = np.array(y_train_data)
# x_val_data = np.array(x_val_data)
# y_val_data = np.array(y_val_data)
# x_test_data = np.array(x_test_data)
# y_test_data = np.array(y_test_data)
        


In [12]:
import concurrent.futures

# Initialize start indices and number of items per worker
train_size = len(x_train)
val_size = len(x_val)
test_size = len(x_test)

P = 48
train_startof=[None]*P
val_startof=[None]*P
test_startof=[None]*P

train_nof=[train_size // P] * P
val_nof=[val_size // P] * P
test_nof=[test_size // P] * P

train_startof[0]=0
val_startof[0]=0
test_startof[0]=0



for i in range(P):
    if i < train_size % P:
        train_nof[i] += 1
    if i < val_size % P:
        val_nof[i] += 1
    if i < test_size % P:
        test_nof[i] += 1
    
    if i > 0:
        train_startof[i] = train_startof[i - 1] + train_nof[i - 1]
        val_startof[i] = val_startof[i - 1] + val_nof[i - 1]
        test_startof[i] = test_startof[i - 1] + test_nof[i - 1]


# Worker function to process a chunk of the data
def worker(tid):
    
    # print(f"Worker {tid} started")
    
    train_start=train_startof[tid]
    train_n=train_nof[tid]
    val_start=val_startof[tid]
    val_n=val_nof[tid]
    test_start=test_startof[tid]
    test_n=test_nof[tid]
    
    train_end=train_start+train_n
    val_end=val_start+val_n
    test_end=test_start+test_n
    
    train_x=[]
    train_y=[]
    val_x=[]
    val_y=[]
    test_x=[]
    test_y=[]
    
    for i in range(train_start, train_end):
        video_path = x_train[i]
        target = y_train[i]
        pose_landmarks,i = apply_mediapipe_pose_v2(video_path,number_of_frames)
        if len(pose_landmarks) == number_of_frames:
            train_x.append(pose_landmarks)
            train_y.append(target)
            
    for i in range(val_start, val_end):
        video_path = x_val[i]
        target = y_val[i]
        pose_landmarks,i = apply_mediapipe_pose_v2(video_path,number_of_frames)
        if len(pose_landmarks) == number_of_frames:
            val_x.append(pose_landmarks)
            val_y.append(target)
            
    for i in range(test_start, test_end):
        video_path = x_test[i]
        target = y_test[i]
        pose_landmarks,i = apply_mediapipe_pose_v2(video_path,number_of_frames)
        if len(pose_landmarks) == number_of_frames:
            test_x.append(pose_landmarks)
            test_y.append(target)
            
    return tid, train_x, train_y, val_x, val_y, test_x, test_y
            
    
 
    # for idx in range(startof[i], startof[i] + nof[i]):
    #     video_path = video_paths[idx]
    #     target = targets[idx]
    #     pose_landmarks = apply_mediapipe_pose(video_path,number_of_frames)
    #     if len(pose_landmarks) == P:
    #         local_x.append(pose_landmarks)
    #         local_y.append(target)
    # return i, local_x, local_y

with concurrent.futures.ThreadPoolExecutor(max_workers=P) as executor:
    results = list(executor.map(worker, range(P)))



I0000 00:00:1745770194.772594 1543188 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1745770194.867853 1543564 gl_context.cc:369] GL version: 3.2 (OpenGL ES 3.2 NVIDIA 535.230.02), renderer: NVIDIA A40/PCIe/SSE2
I0000 00:00:1745770194.898095 1543199 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1745770194.968650 1543613 gl_context.cc:369] GL version: 3.2 (OpenGL ES 3.2 NVIDIA 535.230.02), renderer: NVIDIA A40/PCIe/SSE2
I0000 00:00:1745770194.970565 1543187 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
W0000 00:00:1745770195.002319 1543319 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
I0000 00:00:1745770195.045133 1543622 gl_context.cc:369] GL version: 3.2 (OpenGL ES 3.2 NVIDIA 535.230.02), renderer: NVIDIA A40/PCIe/SSE2
I0000 00:00:1745770195.047125 1543189 gl_context_egl.cc:85] Successfully i

In [13]:
sorted_results = sorted(results, key=lambda x: x[0])

def get_shape(lst):
    if isinstance(lst, list):
        return [len(lst)] + get_shape(lst[0]) if lst else []
    return []

x_train_data = []
y_train_data = []
x_val_data = []
y_val_data = []
x_test_data = []
y_test_data = []

for result in sorted_results:
    i, worker_train_x, worker_train_y, worker_val_x, worker_val_y, worker_test_x, worker_test_y = result
    # Fill the respective ranges in the corresponding arrays
    x_train_data[train_startof[i]:train_startof[i] + train_nof[i]] = worker_train_x
    y_train_data[train_startof[i]:train_startof[i] + train_nof[i]] = worker_train_y
    x_val_data[val_startof[i]:val_startof[i] + val_nof[i]] = worker_val_x
    y_val_data[val_startof[i]:val_startof[i] + val_nof[i]] = worker_val_y
    x_test_data[test_startof[i]:test_startof[i] + test_nof[i]] = worker_test_x
    y_test_data[test_startof[i]:test_startof[i] + test_nof[i]] = worker_test_y

In [15]:

x_train_data = np.array(x_train_data)
y_train_data = np.array(y_train_data)
x_val_data = np.array(x_val_data)
y_val_data = np.array(y_val_data)
x_test_data = np.array(x_test_data)
y_test_data = np.array(y_test_data)

In [14]:
#save data


np.save('x_train_data.npy', x_train_data)
np.save('y_train_data.npy', y_train_data)
np.save('x_val_data.npy', x_val_data)
np.save('y_val_data.npy', y_val_data)
np.save('x_test_data.npy', x_test_data)
np.save('y_test_data.npy', y_test_data)

pose_landmark_channels = x_train_data.shape[3]

AttributeError: 'list' object has no attribute 'shape'

In [17]:
pose_landmark_channels = x_train_data.shape[3]

In [5]:
def hip_center_and_normalize(pl):
   
    data=pl.copy()
    coordinates = data[:, :, :, :3]  
    visibility = data[:, :, :, 3:4]  
    presence = data[:, :, :, 4:5]  

    
    left_hip = coordinates[:, :, 23, :] 
    right_hip = coordinates[:, :, 24, :] 
    hip_center = (left_hip + right_hip) / 2 
    # hip_center_z=hip_center[:,:,2]

    # batch , n_frames, n_landmarks, 5

    centered_coords = coordinates.copy()
    

    hip_center = hip_center[:, :, None, :]
    centered_coords -= hip_center

    
    x_values = centered_coords[:, :, :, 0]  
    y_values = centered_coords[:, :, :, 1]  
    z_values = centered_coords[:, :, :, 2]  
    
    x_min=np.min(x_values,keepdims=True,axis=2)
    x_max=np.max(x_values,keepdims=True,axis=2)
    x_size=np.abs(x_max-x_min)
    x_max_size=np.max(x_size,keepdims=True,axis=1)
    
    y_min=np.min(y_values,keepdims=True,axis=2)
    y_max=np.max(y_values,keepdims=True,axis=2)
    y_size=np.abs(y_max-y_min)
    y_max_size=np.max(y_size,keepdims=True,axis=1)
    
    z_min=np.min(z_values,keepdims=True,axis=2)
    z_max=np.max(z_values,keepdims=True,axis=2)
    z_size=np.abs(z_max-z_min)   
    z_max_size=np.max(z_size,keepdims=True,axis=1)


    epsilon = 1e-8
    
    x_values /= (x_max_size + epsilon)
    y_values /= (y_max_size + epsilon)
    z_values /= (z_max_size + epsilon)
    
    centered_coords[:, :, :, 0] = x_values
    centered_coords[:, :, :, 1] = y_values
    centered_coords[:, :, :, 2] = z_values
    
    processed_data = np.concatenate([centered_coords, visibility, presence], axis=3)

    return processed_data

In [6]:
#load data


x_train_data = np.load('x_train_data.npy', allow_pickle=True)
y_train_data = np.load('y_train_data.npy', allow_pickle=True)
x_val_data = np.load('x_val_data.npy', allow_pickle=True)
y_val_data = np.load('y_val_data.npy', allow_pickle=True)
x_test_data = np.load('x_test_data.npy', allow_pickle=True)
y_test_data = np.load('y_test_data.npy', allow_pickle=True)

pose_landmark_channels = x_train_data.shape[3]

In [48]:
print(x_train_data.shape)
x_coords=x_train_data[:,:,:,1]

min_val = np.min(x_coords,axis=(0,1,2), keepdims=True)
print(min_val.shape)
print(min_val)


(2156, 15, 33, 5)
(1, 1, 1)
[[[-3.01563501]]]


In [2]:
x_test_data = np.load('x_test_data.npy', allow_pickle=True)
y_test_data = np.load('y_test_data.npy', allow_pickle=True)

NameError: name 'np' is not defined

In [65]:
x_train_data.shape, y_train_data.shape, x_val_data.shape, y_val_data.shape, x_test_data.shape, y_test_data.shape

((2156, 15, 33, 5),
 (2156,),
 (888, 15, 33, 5),
 (888,),
 (531, 15, 33, 5),
 (531,))

In [8]:
x_train_data=hip_center_and_normalize(x_train_data)
x_val_data=hip_center_and_normalize(x_val_data)
x_test_data=hip_center_and_normalize(x_test_data)

In [9]:
x_train_data.shape, y_train_data.shape, x_val_data.shape, y_val_data.shape, x_test_data.shape, y_test_data.shape

((2156, 15, 33, 5),
 (2156,),
 (888, 15, 33, 5),
 (888,),
 (531, 15, 33, 5),
 (531,))

In [10]:
# reshape data
# x_train_reshaped = np.array(x_train).reshape(len(x_train), number_of_frames,33*3).astype('float32')
# x_val_reshaped = np.array(x_val).reshape(len(x_val), number_of_frames,33*3).astype('float32')
# x_test_reshaped = np.array(x_test).reshape(len(x_test), number_of_frames,33*3).astype('float32')
number_of_frames=15
x_train_reshaped = x_train_data.reshape(x_train_data.shape[0], number_of_frames,33*pose_landmark_channels).astype('float32')
x_val_reshaped = x_val_data.reshape(x_val_data.shape[0], number_of_frames,33*pose_landmark_channels).astype('float32')
x_test_reshaped = x_test_data.reshape(x_test_data.shape[0], number_of_frames,33*pose_landmark_channels).astype('float32')

In [48]:
x_test_data.shape

(531, 15, 33, 5)

In [69]:
x_train_reshaped.shape, x_val_reshaped.shape, x_test_reshaped.shape

((2156, 15, 165), (888, 15, 165), (531, 15, 165))

In [12]:
from keras.layers import LSTM, Dense, Input,Dropout
from keras.models import Model

input_shape = x_train_reshaped.shape[1:]


def create_lstm_model(input_shape):
    input=Input(shape=input_shape)
    x=LSTM(256, return_sequences=True)(input)
    x=Dropout(0.2)(x)
    x=LSTM(256, return_sequences=True)(x)
    x=Dropout(0.2)(x)
    x=LSTM(128)(x)
    x=Dense(128, activation='relu')(x)
    output=Dense(num_classes, activation='softmax')(x)
    model=Model(inputs=input,outputs=output)
    
    
    model.compile(optimizer='adam', 
              loss='sparse_categorical_crossentropy', 
              metrics=['accuracy'])
    
    return model


In [13]:
from tensorflow.keras.callbacks import ModelCheckpoint,EarlyStopping

# model.compile(optimizer='adam',loss='sparse_categorical_crossentropy',metrics=['accuracy']) 

early_stopping_callback = EarlyStopping(
    monitor='val_loss', 
    patience=10, 
    restore_best_weights=True, 
    verbose=1
)

checkpoint_callback = ModelCheckpoint(
    filepath='mediapipe_lstm_nonpadded.keras',
    monitor='val_accuracy',
    save_best_only=True,
    save_weights_only=False,
    mode='max',
    verbose=1
)


In [14]:
model=create_lstm_model(x_train_reshaped.shape[1:])

model.fit(x_train_reshaped, y_train_data,
            validation_data=(x_val_reshaped, y_val_data),
            epochs=500,
            batch_size=16,
            callbacks=[early_stopping_callback, checkpoint_callback],
            verbose=1)  

Epoch 1/500


W0000 00:00:1748100851.745884  823123 gpu_device.cc:2344] Cannot dlopen some GPU libraries. Please make sure the missing libraries mentioned above are installed properly if you would like to use GPU. Follow the guide at https://www.tensorflow.org/install/gpu for how to download and setup the required libraries for your platform.
Skipping registering GPU devices...


135/135 ━━━━━━━━━━━━━━━━━━━━ 0s 57ms/step - accuracy: 0.0752 - loss: 3.5988
Epoch 1: val_accuracy improved from -inf to 0.13851, saving model to mediapipe_lstm_nonpadded.keras
135/135 ━━━━━━━━━━━━━━━━━━━━ 12s 68ms/step - accuracy: 0.0755 - loss: 3.5971 - val_accuracy: 0.1385 - val_loss: 3.0602
Epoch 2/500
135/135 ━━━━━━━━━━━━━━━━━━━━ 0s 56ms/step - accuracy: 0.1966 - loss: 2.9307
Epoch 2: val_accuracy improved from 0.13851 to 0.24550, saving model to mediapipe_lstm_nonpadded.keras
135/135 ━━━━━━━━━━━━━━━━━━━━ 9s 65ms/step - accuracy: 0.1968 - loss: 2.9300 - val_accuracy: 0.2455 - val_loss: 2.6985
Epoch 3/500
134/135 ━━━━━━━━━━━━━━━━━━━━ 0s 56ms/step - accuracy: 0.2742 - loss: 2.5505
Epoch 3: val_accuracy improved from 0.24550 to 0.28604, saving model to mediapipe_lstm_nonpadded.keras
135/135 ━━━━━━━━━━━━━━━━━━━━ 9s 64ms/step - accuracy: 0.2745 - loss: 2.5492 - val_accuracy: 0.2860 - val_loss: 2.4443
Epoch 4/500
134/135 ━━━━━━━━━━━━━━━━━━━━ 0s 56ms/step - accuracy: 0.3450 - loss: 2.2860

In [15]:
model.evaluate(x_test_reshaped, y_test_data, verbose=1)

17/17 ━━━━━━━━━━━━━━━━━━━━ 0s 28ms/step - accuracy: 0.5350 - loss: 1.7463


[1.5603183507919312, 0.5819209218025208]

In [ ]:

model=keras.models.load_model('mediapipe_lstm_nonpadded.keras')

test_loss, test_accuracy = model.evaluate(x_test_reshaped, y_test_data, verbose=1)
print(f"Test Loss: {test_loss:.4f}")     
print(f"Test Accuracy: {test_accuracy:.4f}")

17/17 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.5733 - loss: 2.0715
Test Loss: 1.8651
Test Accuracy: 0.6064


In [ ]:
#best

model=keras.models.load_model('mediapipe_lstm_nonpadded.keras')

test_loss, test_accuracy = model.evaluate(x_test_reshaped, y_test_data, verbose=1)
print(f"Test Loss: {test_loss:.4f}")
print(f"Test Accuracy: {test_accuracy:.4f}")

17/17 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.5607 - loss: 2.2152
Test Loss: 1.8778
Test Accuracy: 0.6102


In [33]:


model = create_lstm_model(input_shape, num_classes)  

model.compile(optimizer='adam',loss='sparse_categorical_crossentropy',metrics=[
        'accuracy'
        
    ] ) 
history = model.fit(x_train_reshaped, y_train_data,
                    validation_data=(x_val_reshaped, y_val_data),
                    epochs=200,
                    batch_size=32,
                    callbacks=[early_stopping_callback, checkpoint_callback],
                    verbose=1)

Epoch 1/200
67/68 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step - accuracy: 0.0387 - loss: 3.8292
Epoch 1: val_accuracy did not improve from 0.58559
68/68 ━━━━━━━━━━━━━━━━━━━━ 7s 61ms/step - accuracy: 0.0390 - loss: 3.8267 - val_accuracy: 0.0811 - val_loss: 3.5678
Epoch 2/200
67/68 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step - accuracy: 0.0869 - loss: 3.5218
Epoch 2: val_accuracy did not improve from 0.58559
68/68 ━━━━━━━━━━━━━━━━━━━━ 4s 56ms/step - accuracy: 0.0873 - loss: 3.5187 - val_accuracy: 0.1498 - val_loss: 3.2660
Epoch 3/200
67/68 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step - accuracy: 0.1551 - loss: 3.1767
Epoch 3: val_accuracy did not improve from 0.58559
68/68 ━━━━━━━━━━━━━━━━━━━━ 4s 55ms/step - accuracy: 0.1550 - loss: 3.1765 - val_accuracy: 0.1644 - val_loss: 3.1226
Epoch 4/200
67/68 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step - accuracy: 0.1773 - loss: 3.0418
Epoch 4: val_accuracy did not improve from 0.58559
68/68 ━━━━━━━━━━━━━━━━━━━━ 4s 55ms/step - accuracy: 0.1776 - loss: 3.0403 - val_accuracy: 0.1903 - val_l

In [30]:
# play video
def play_video(video_path):
    cap = cv2.VideoCapture(video_path)
    
    if not cap.isOpened():
        print("Error: Could not open video.")
        return

    while True:
        ret, frame = cap.read()
        if not ret:
            break

        cv2.imshow('Video', frame)
        if cv2.waitKey(10) & 0xFF == ord('q'):
            break

    cap.release()
    cv2.destroyAllWindows()

In [57]:
#load model
model = keras.models.load_model('mediapipe_model_full.keras')

model.evaluate(x_test_reshaped, y_test_data, verbose=1)


27/27 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.3058 - loss: 2.8242


[2.539442300796509, 0.3666274845600128]